In [1]:
import os
from joblib import Parallel, delayed
import time
import numpy as np
import pickle
import pylab as pl
import pandas as pd

# import jupyternotify
import subprocess
import concurrent.futures
import shutil

In [2]:
regions = ['us-central1-a', 'europe-west3-c', 'asia-south1-c', 'us-central1-a', 'europe-west3-c', 'asia-south1-c']

In [3]:
for i in range(len(regions)):
    

    cmd = 'gcloud compute instances create flwr-'+f"{i:03}"+' \
    --project=ucr-ursa-major-lesani-lab \
    --zone='+regions[i]+' \
    --machine-type=e2-medium \
    --network-interface=network-tier=PREMIUM,stack-type=IPV4_ONLY,subnet=default \
    --maintenance-policy=MIGRATE \
    --provisioning-model=STANDARD \
    --service-account=961693926925-compute@developer.gserviceaccount.com \
    --scopes=https://www.googleapis.com/auth/devstorage.read_only,https://www.googleapis.com/auth/logging.write,https://www.googleapis.com/auth/monitoring.write,https://www.googleapis.com/auth/service.management.readonly,https://www.googleapis.com/auth/servicecontrol,https://www.googleapis.com/auth/trace.append \
    --create-disk=auto-delete=yes,boot=yes,device-name=instance-20240829-120659,image=projects/debian-cloud/global/images/debian-12-bookworm-v20240815,mode=rw,size=30,type=pd-balanced \
    --no-shielded-secure-boot \
    --shielded-vtpm \
    --shielded-integrity-monitoring \
    --labels=goog-ec-src=vm_add-gcloud \
    --reservation-affinity=any'
    
    os.system(cmd)

Created [https://www.googleapis.com/compute/v1/projects/ucr-ursa-major-lesani-lab/zones/us-central1-a/instances/flwr-000].
 - Disk size: '30 GB' is larger than image size: '10 GB'. You might need to resize the root repartition manually if the operating system does not support automatic resizing. See https://cloud.google.com/compute/docs/disks/add-persistent-disk#resize_pd for details.



NAME      ZONE           MACHINE_TYPE  PREEMPTIBLE  INTERNAL_IP    EXTERNAL_IP      STATUS
flwr-000  us-central1-a  e2-medium                  10.128.15.210  104.155.186.172  RUNNING


Created [https://www.googleapis.com/compute/v1/projects/ucr-ursa-major-lesani-lab/zones/europe-west3-c/instances/flwr-001].
 - Disk size: '30 GB' is larger than image size: '10 GB'. You might need to resize the root repartition manually if the operating system does not support automatic resizing. See https://cloud.google.com/compute/docs/disks/add-persistent-disk#resize_pd for details.



NAME      ZONE            MACHINE_TYPE  PREEMPTIBLE  INTERNAL_IP  EXTERNAL_IP    STATUS
flwr-001  europe-west3-c  e2-medium                  10.156.0.35  34.159.31.246  RUNNING


Created [https://www.googleapis.com/compute/v1/projects/ucr-ursa-major-lesani-lab/zones/asia-south1-c/instances/flwr-002].
 - Disk size: '30 GB' is larger than image size: '10 GB'. You might need to resize the root repartition manually if the operating system does not support automatic resizing. See https://cloud.google.com/compute/docs/disks/add-persistent-disk#resize_pd for details.



...

NAME      ZONE           MACHINE_TYPE  PREEMPTIBLE  INTERNAL_IP    EXTERNAL_IP   STATUS
flwr-003  us-central1-a  e2-medium                  10.128.15.217  34.132.137.6  RUNNING


Created [https://www.googleapis.com/compute/v1/projects/ucr-ursa-major-lesani-lab/zones/europe-west3-c/instances/flwr-004].
 - Disk size: '30 GB' is larger than image size: '10 GB'. You might need to resize the root repartition manually if the operating system does not support automatic resizing. See https://cloud.google.com/compute/docs/disks/add-persistent-disk#resize_pd for details.



NAME      ZONE            MACHINE_TYPE  PREEMPTIBLE  INTERNAL_IP  EXTERNAL_IP   STATUS
flwr-004  europe-west3-c  e2-medium                  10.156.0.39  35.198.72.77  RUNNING


Created [https://www.googleapis.com/compute/v1/projects/ucr-ursa-major-lesani-lab/zones/asia-south1-c/instances/flwr-005].
 - Disk size: '30 GB' is larger than image size: '10 GB'. You might need to resize the root repartition manually if the operating system does not support automatic resizing. See https://cloud.google.com/compute/docs/disks/add-persistent-disk#resize_pd for details.



NAME      ZONE           MACHINE_TYPE  PREEMPTIBLE  INTERNAL_IP  EXTERNAL_IP     STATUS
flwr-005  asia-south1-c  e2-medium                  10.160.0.74  35.200.186.214  RUNNING


In [5]:
time.sleep(30)

In [6]:
os.system('git add .; git commit -m "fc"; git push origin')

On branch main
Your branch is up to date with 'origin/main'.

nothing to commit, working tree clean


Everything up-to-date


0

In [7]:
def initialize(i):
    command = 'gcloud compute ssh --zone "'+regions[i]+'" "flwr-'+f"{i:03}"+'" --project "ucr-ursa-major-lesani-lab" --command "sudo apt -y install git; git clone https://github.com/tejas-shivanand-mane/flower.git;cd flower"'
    os.system(command)

In [8]:
def git_pull(i):
    command = 'gcloud compute ssh --zone "'+regions[i]+'" "flwr-'+f"{i:03}"+'" --project "ucr-ursa-major-lesani-lab" --command "cd flower; git pull;"'
    os.system(command)

In [9]:
def setup(i):
    command = 'gcloud compute ssh --zone "'+regions[i]+'" "flwr-'+f"{i:03}"+'" --project "ucr-ursa-major-lesani-lab" --command "cd flower; sudo sh setup.sh"'
    os.system(command)

In [10]:
def clean(i):
    command = 'gcloud compute ssh --zone "us-central1-a" "flwr-'+f"{i:03}"+'" --project "ucr-ursa-major-lesani-lab" --command "sudo rm -r flower"'
    os.system(command)

In [ ]:
time.sleep(45)

In [11]:
results = Parallel(n_jobs=60)(delayed(initialize)(i) for i in range(len(regions)))

Reading package lists...

Reading package lists...


Building dependency tree...
Reading state information...

Building dependency tree...The following additional packages will be installed:
  git-man liberror-perl patch
Suggested packages:
  git-daemon-run | git-daemon-sysvinit git-doc git-email git-gui gitk gitweb
  git-cvs git-mediawiki git-svn ed diffutils-doc
The following NEW packages will be installed:
  git git-man liberror-perl patch
0 upgraded, 4 newly installed, 0 to remove and 0 not upgraded.
Need to get 9377 kB of archives.
After this operation, 48.0 MB of additional disk space will be used.
Get:1 file:/etc/apt/mirrors/debian.list Mirrorlist [30 B]

Reading state information...
Get:2 https://deb.debian.org/debian bookworm/main amd64 liberror-perl all 0.17029-2 [29.0 kB]
Get:3 https://deb.debian.org/debian bookworm/main amd64 git-man all 1:2.39.2-1.1 [2049 kB]
Reading package lists...The following additional packages will be installed:
  git-man liberror-perl patch
Suggested packages:
  git-daemon-run | git-daemon-sysvinit g

0 upgraded, 4 newly installed, 0 to remove and 0 not upgraded.
Need to get 9377 kB of archives.
After this operation, 48.0 MB of additional disk space will be used.
Get:1 file:/etc/apt/mirrors/debian.list Mirrorlist [30 B]
Reading package lists...Get:4 https://deb.debian.org/debian bookworm/main amd64 git amd64 1:2.39.2-1.1 [7171 kB]
Get:2 https://deb.debian.org/debian bookworm/main amd64 liberror-perl all 0.17029-2 [29.0 kB]
Get:3 https://deb.debian.org/debian bookworm/main amd64 git-man all 1:2.39.2-1.1 [2049 kB]
Get:5 https://deb.debian.org/debian bookworm/main amd64 patch amd64 2.7.6-7 [128 kB]
Get:4 https://deb.debian.org/debian bookworm/main amd64 git amd64 1:2.39.2-1.1 [7171 kB]
Get:5 https://deb.debian.org/debian bookworm/main amd64 patch amd64 2.7.6-7 [128 kB]
Reading package lists...



debconf: unable to initialize frontend: Dialog
debconf: (Dialog frontend will not work on a dumb terminal, an emacs shell buffer, or without a controlling terminal.)
debconf: falling back to frontend: Readline
debconf: unable to initialize frontend: Readline
debconf: (This frontend requires a controlling tty.)
debconf: falling back to frontend: Teletype
dpkg-preconfigure: unable to re-open stdin: 
debconf: unable to initialize frontend: Dialog
debconf: (Dialog frontend will not work on a dumb terminal, an emacs shell buffer, or without a controlling terminal.)
debconf: falling back to frontend: Readline
debconf: unable to initialize frontend: Readline
debconf: (This frontend requires a controlling tty.)
debconf: falling back to frontend: Teletype
dpkg-preconfigure: unable to re-open stdin: 


...

debconf: unable to initialize frontend: Dialog
debconf: (Dialog frontend will not work on a dumb terminal, an emacs shell buffer, or without a controlling terminal.)
debconf: falling back to frontend: Readline
debconf: unable to initialize frontend: Readline
debconf: (This frontend requires a controlling tty.)
debconf: falling back to frontend: Teletype
dpkg-preconfigure: unable to re-open stdin: 


Fetched 9377 kB in 10s (909 kB/s)
Selecting previously unselected package liberror-perl.
(Reading database ... 69231 files and directories currently installed.)
Preparing to unpack .../liberror-perl_0.17029-2_all.deb ...
Unpacking liberror-perl (0.17029-2) ...
Selecting previously unselected package git-man.
Preparing to unpack .../git-man_1%3a2.39.2-1.1_all.deb ...
Unpacking git-man (1:2.39.2-1.1) ...
Selecting previously unselected package git.
Preparing to unpack .../git_1%3a2.39.2-1.1_amd64.deb ...
Unpacking git (1:2.39.2-1.1) ...


Cloning into 'flower'...


Selecting previously unselected package patch.
Preparing to unpack .../patch_2.7.6-7_amd64.deb ...
Unpacking patch (2.7.6-7) ...
Setting up liberror-perl (0.17029-2) ...
Setting up patch (2.7.6-7) ...
Setting up git-man (1:2.39.2-1.1) ...
Setting up git (1:2.39.2-1.1) ...
Processing triggers for man-db (2.11.2-2) ...


Cloning into 'flower'...
Cloning into 'flower'...
Cloning into 'flower'...
Cloning into 'flower'...
Cloning into 'flower'...


In [18]:
os.system('git add .; git commit -m "fc"; git push origin')
results = Parallel(n_jobs=60)(delayed(git_pull)(i) for i in range(len(regions)))

[main fe8dc159] fc
 4 files changed, 106958 insertions(+), 62 deletions(-)


To github.com:tejas-shivanand-mane/flower.git
   07847634..fe8dc159  main -> main
From https://github.com/tejas-shivanand-mane/flower
   07847634..fe8dc159  main       -> origin/main
From https://github.com/tejas-shivanand-mane/flower
   07847634..fe8dc159  main       -> origin/main


Updating 07847634..fe8dc159
Fast-forward
 .../pytorch-from-centralized-to-federated/cifar.py |      2 +-
 .../client.py                                      |      6 +-
 .../server.py                                      |      4 +-
 flwr.ipynb                                         | 107008 +++++++++++++++++-
 4 files changed, 106958 insertions(+), 62 deletions(-)


From https://github.com/tejas-shivanand-mane/flower
   07847634..fe8dc159  main       -> origin/main


Updating 07847634..fe8dc159
Fast-forward
 .../pytorch-from-centralized-to-federated/cifar.py |      2 +-
 .../client.py                                      |      6 +-
 .../server.py                                      |      4 +-
 flwr.ipynb                                         | 107008 +++++++++++++++++-
 4 files changed, 106958 insertions(+), 62 deletions(-)


...

Updating 07847634..fe8dc159
Fast-forward
 .../pytorch-from-centralized-to-federated/cifar.py |      2 +-
 .../client.py                                      |      6 +-
 .../server.py                                      |      4 +-
 flwr.ipynb                                         | 107008 +++++++++++++++++-
 4 files changed, 106958 insertions(+), 62 deletions(-)


From https://github.com/tejas-shivanand-mane/flower
   07847634..fe8dc159  main       -> origin/main


Updating 07847634..fe8dc159
Fast-forward
 .../pytorch-from-centralized-to-federated/cifar.py |      2 +-
 .../client.py                                      |      6 +-
 .../server.py                                      |      4 +-
 flwr.ipynb                                         | 107008 +++++++++++++++++-
 4 files changed, 106958 insertions(+), 62 deletions(-)


From https://github.com/tejas-shivanand-mane/flower
   07847634..fe8dc159  main       -> origin/main


Updating 07847634..fe8dc159
Fast-forward
 .../pytorch-from-centralized-to-federated/cifar.py |      2 +-
 .../client.py                                      |      6 +-
 .../server.py                                      |      4 +-
 flwr.ipynb                                         | 107008 +++++++++++++++++-
 4 files changed, 106958 insertions(+), 62 deletions(-)
Updating 07847634..fe8dc159
Fast-forward
 .../pytorch-from-centralized-to-federated/cifar.py |      2 +-
 .../client.py                                      |      6 +-
 .../server.py                                      |      4 +-
 flwr.ipynb                                         | 107008 +++++++++++++++++-
 4 files changed, 106958 insertions(+), 62 deletions(-)


In [13]:
results = Parallel(n_jobs=60)(delayed(setup)(i) for i in range(len(regions)))

Get:1 file:/etc/apt/mirrors/debian.list Mirrorlist [30 B]
Get:1 file:/etc/apt/mirrors/debian.list Mirrorlist [30 B]
Get:5 file:/etc/apt/mirrors/debian-security.list Mirrorlist [39 B]
Get:5 file:/etc/apt/mirrors/debian-security.list Mirrorlist [39 B]
Get:7 https://packages.cloud.google.com/apt google-compute-engine-bookworm-stable InRelease [1321 B]
Get:7 https://packages.cloud.google.com/apt google-compute-engine-bookworm-stable InRelease [1321 B]
Get:8 https://packages.cloud.google.com/apt cloud-sdk-bookworm InRelease [1654 B]
Get:8 https://packages.cloud.google.com/apt cloud-sdk-bookworm InRelease [1654 B]
Get:2 https://deb.debian.org/debian bookworm InRelease [151 kB]
Get:2 https://deb.debian.org/debian bookworm InRelease [151 kB]
Get:9 https://packages.cloud.google.com/apt google-compute-engine-bookworm-stable/main amd64 Packages [3128 B]
Get:3 https://deb.debian.org/debian bookworm-updates InRelease [55.4 kB]
Get:3 https://deb.debian.org/debian bookworm-updates InRelease [55.4 kB]

Get:1 file:/etc/apt/mirrors/debian.list Mirrorlist [30 B]
Get:4 file:/etc/apt/mirrors/debian-security.list Mirrorlist [39 B]
Get:2 https://deb.debian.org/debian bookworm InRelease [151 kB]
Get:7 https://packages.cloud.google.com/apt google-compute-engine-bookworm-stable InRelease [1321 B]
Get:3 https://deb.debian.org/debian bookworm-updates InRelease [55.4 kB]
Get:5 https://deb.debian.org/debian bookworm-backports InRelease [56.6 kB]
Get:6 https://deb.debian.org/debian-security bookworm-security InRelease [48.0 kB]
Get:8 https://packages.cloud.google.com/apt cloud-sdk-bookworm InRelease [1654 B]


Get:1 file:/etc/apt/mirrors/debian.list Mirrorlist [30 B]
Get:9 https://packages.cloud.google.com/apt google-compute-engine-bookworm-stable/main amd64 Packages [3128 B]
Get:5 file:/etc/apt/mirrors/debian-security.list Mirrorlist [39 B]
Get:2 https://deb.debian.org/debian bookworm InRelease [151 kB]
Get:7 https://packages.cloud.google.com/apt google-compute-engine-bookworm-stable InRelease [1321 B]
Get:3 https://deb.debian.org/debian bookworm-updates InRelease [55.4 kB]
Get:15 https://deb.debian.org/debian bookworm-backports/main Sources.diff/Index [63.3 kB]
Get:4 https://deb.debian.org/debian bookworm-backports InRelease [56.6 kB]
Get:6 https://deb.debian.org/debian-security bookworm-security InRelease [48.0 kB]
Get:16 https://deb.debian.org/debian bookworm-backports/main amd64 Packages.diff/Index [63.3 kB]
Get:10 https://deb.debian.org/debian bookworm/main Sources [9487 kB]
Get:17 https://deb.debian.org/debian bookworm-backports/main Translation-en.diff/Index [63.3 kB]
Get:8 https://p

Get:6 https://deb.debian.org/debian-security bookworm-security InRelease [48.0 kB]
Get:8 https://packages.cloud.google.com/apt cloud-sdk-bookworm InRelease [1654 B]
Get:9 https://deb.debian.org/debian bookworm/main Sources [9487 kB]
Get:1 file:/etc/apt/mirrors/debian.list Mirrorlist [30 B]
Get:5 file:/etc/apt/mirrors/debian-security.list Mirrorlist [39 B]


Get:7 https://packages.cloud.google.com/apt google-compute-engine-bookworm-stable InRelease [1321 B]
Get:18 https://deb.debian.org/debian-security bookworm-security/main Sources [109 kB]
Get:19 https://deb.debian.org/debian-security bookworm-security/main amd64 Packages [179 kB]
Get:20 https://deb.debian.org/debian-security bookworm-security/main Translation-en [108 kB]
Get:2 https://deb.debian.org/debian bookworm InRelease [151 kB]
Get:12 https://packages.cloud.google.com/apt google-compute-engine-bookworm-stable/main amd64 Packages [3128 B]
Get:8 https://packages.cloud.google.com/apt cloud-sdk-bookworm InRelease [1654 B]
Get:3 https://deb.debian.org/debian bookworm-updates InRelease [55.4 kB]
Get:4 https://deb.debian.org/debian bookworm-backports InRelease [56.6 kB]
Get:10 https://deb.debian.org/debian bookworm/main amd64 Packages [8787 kB]
Get:6 https://deb.debian.org/debian-security bookworm-security InRelease [48.0 kB]
Get:9 https://packages.cloud.google.com/apt google-compute-eng

...

Preparing transaction: ...working... done
Verifying transaction: ...working... done
Executing transaction: ...working... done



## Package Plan ##

  environment location: /home/tejas/anaconda3

  added / updated specs:
    - cpuonly
    - pytorch
    - torchaudio
    - torchvision


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2024.7.2   |       h06a4308_0         127 KB
    certifi-2024.8.30          |  py312h06a4308_0         163 KB
    conda-24.7.1               |  py312h06a4308_0         1.2 MB
    cpuonly-2.0                |                0           2 KB  pytorch
    ffmpeg-4.3                 |       hf484d3e_0         9.9 MB  pytorch
    gmp-6.2.1                  |       h295c915_3         544 KB
    gnutls-3.6.15              |       he1e5248_0         1.0 MB
    lame-3.100                 |       h7b6447c_0         323 KB
    libidn2-2.3.4              |       h5eee18b_0         146 KB
    libjpeg-turbo-2.0.0        |       h9bf148f_0         950 KB  pytorch
    libtasn1-4.19.0  

Preparing transaction: ...working... done
Verifying transaction: ...working... 

done
done
Executing transaction: ...working... done
Executing transaction: ...working... done
done



## Package Plan ##

  environment location: /home/tejas/anaconda3

  added / updated specs:
    - cpuonly
    - pytorch
    - torchaudio
    - torchvision


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2024.7.2   |       h06a4308_0         127 KB
    certifi-2024.8.30          |  py312h06a4308_0         163 KB
    conda-24.7.1               |  py312h06a4308_0         1.2 MB
    cpuonly-2.0                |                0           2 KB  pytorch
    ffmpeg-4.3                 |       hf484d3e_0         9.9 MB  pytorch
    gmp-6.2.1                  |       h295c915_3         544 KB
    gnutls-3.6.15              |       he1e5248_0         1.0 MB
    lame-3.100                 |       h7b6447c_0         323 KB
    libidn2-2.3.4              |       h5eee18b_0         146 KB
    libjpeg-turbo-2.0.0        |       h9bf148f_0         950 KB  pytorch
    libtasn1-4.19.0  

In [ ]:
# results = Parallel(n_jobs=60)(delayed(clean)(i) for i in range(3))

In [23]:

def run_server(i):
    command = 'gcloud compute ssh --zone "'+regions[i]+'" "flwr-'+f"{i:03}"+\
    '" --project "ucr-ursa-major-lesani-lab" --command "cd flower/examples/pytorch-from-centralized-to-federated/; sh server_job.sh"'
    os.system(command)

def run_client(i):
    if i!=0:
        command = 'gcloud compute ssh --zone "'+regions[i]+'" "flwr-'+f"{i:03}"+\
        '" --project "ucr-ursa-major-lesani-lab" --command "cd flower/examples/pytorch-from-centralized-to-federated/; sh client_job.sh '+str(i-1)+'"'
        os.system(command)
    
    
def kill_all(i):
    command = 'gcloud compute ssh --zone "'+regions[i]+'" "flwr-'+f"{i:03}"+\
    '" --project "ucr-ursa-major-lesani-lab" --command "sudo killall python"'
    os.system(command)

In [21]:
results = Parallel(n_jobs=60)(delayed(kill_all)(i) for i in range(len(regions)-1))

python: no process found
python: no process found
python: no process found
python: no process found


In [24]:
run_server(0)

In [25]:
results = Parallel(n_jobs=60)(delayed(run_client)(i) for i in range(len(regions)))

In [ ]:
time.sleep(360)

In [ ]:
for i in range(len(regions)):
    command = 'gcloud compute scp --zone "'+regions[i] +'"'+' flwr-'+f"{i:03}"+\
    ':/home/tejas/flower/examples/pytorch-from-centralized-to-federated/nohup.out ../flwr_exps/out_'+str(i)+'.txt'
    os.system(command)

In [ ]:
file_path = '../flwr_exps/out_1.txt'

# Read the file and filter lines containing "test printout"
with open(file_path, 'r') as file:
    lines_with_test_printout = [line.strip() for line in file if "test printout" in line]

# Output the filtered lines
print(lines_with_test_printout)

import re


# Regex pattern to extract accuracy and time
pattern = r"accuracy: ([\d.]+), time: ([\d.]+)"

# Extract accuracy and time using regex
results = []
for line in lines_with_test_printout:
    match = re.search(pattern, line)
    if match:
        accuracy = float(match.group(1))
        time_taken = float(match.group(2))
        results.append((accuracy, time_taken))

# Output the extracted values
print(results)

results_local = np.array(results)

In [ ]:
# pl.figure(figsize = (6,4))
# pl.plot(np.array(list(results_local[:,1])), np.array(list(results_local[:,0])), '-*', label = 'local 1')
# pl.plot(np.array(list(results_local1[:,1])), np.array(list(results_local1[:,0])), '-*', label = 'local 2')

# pl.plot(np.array(list(results_geo[:,1])), np.array(list(results_geo[:,0])), '-*', label = 'geo')
# pl.legend()
# pl.ylabel('Training accuracy')

# pl.xlabel('time (sec)')
# pl.show()
# pl.clf()